# Bias correlations between precip, temp, and snow cover 

<div class="alert alert-block alert-success"; background-color:red> describe notebook ... </div> 

## Load required libraries

In [1]:
import numpy as np   
import pandas as pd     
import netCDF4 as nc            
from netCDF4 import Dataset        
import matplotlib.pyplot as plt            
import xarray as xr            
import cartopy.crs as ccrs        
import cartopy          
import os        
import xesmf as xe       
from cartopy.feature import NaturalEarthFeature     
import cartopy.crs as ccrs 
import cartopy.feature as cf
from cartopy.util import add_cyclic_point
from cartopy.mpl.ticker import LongitudeFormatter, LatitudeFormatter
from scipy.stats import pearsonr
import seaborn as sns

## For parallelisation

In [2]:
from dask.distributed import Client
client = Client(n_workers=16, threads_per_worker=2, memory_limit='32GB')
client

/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/distributed/node.py:182: UserWarning: Port 8787 is already in use.
Perhaps you already have a cluster running?
Hosting the HTTP server on port 37977 instead
  warnings.warn(


<Client: 'tcp://127.0.0.1:42765' processes=16 threads=32, memory=476.84 GiB>

## Set variables

In [3]:
# Bound of altitude inside it we calculate bias correlations 
bound = '1000m_5000m' # This means, altitude > 1000m 
alt_min = 1000    
alt_max = 5000       

# Set product to be the reference 
ref = 'era5'          #  era5_land 

"""
We define the thresholds used to filter smal values of snow cover fraction. 
if threshold==0, that means that we consider values higher or equal to 0%. If threshold is
equal to 1, 3, or 5, that means we consider snc (snow cover) strictly higher than threshold.  
"""

threshold = '0'

# Cold months  
months = [11,12,1,2,3,4]
months_titles = {11:'November',12:'December',1:'January',2:'February',
                 3:'March',4:'April'}      

latlim = slice(30,34.5)
lonlim = slice(-10, -2)
period = slice('1982-01-01', '2014-12-31')

# Set input data paths 
path_cmip6_raw_data = '/home/hchaabani/Data/Snow/snc/cmip6/raw_data'
path_cmip6_snc = '/home/hchaabani/Data/Snow/snc/cmip6/modified_data/monthly/monthly_values_plus_alt/threshold_'+ threshold
path_era5_snc = '/home/hchaabani/Data/Snow/snc/Reanalysis/ERA5/modified_data/monthly/monthly_values_plus_alt/threshold_'+ threshold
path_era5_land_snc = '/home/hchaabani/Data/Snow/snc/Reanalysis/ERA-LAND/modified_data/monthly/monthly_values_plus_alt/threshold_'+threshold
path_SIM_35km_snc = '/home/hchaabani/Data/Snow/snc/SIM_35km/Modified_data/monthly/monthly_values_plus_alt/threshold_'+threshold

path_cmip6_pr = '/home/hchaabani/Data/pr/cmip6/modified_data/monthly_values_plus_alt'
path_era5_pr = '/home/hchaabani/Data/pr/reanalysis/era5/modified_data/monthly_values_plus_alt'
path_era5_land_pr = '/home/hchaabani/Data/pr/reanalysis/era5_land/modified_data/monthly_values_plus_alt'
path_SIM_35km_pr = '/home/hchaabani/Data/pr/SIM_35km/modified_data/monthly_values_plus_alt'

path_cmip6_tas = '/home/hchaabani/Data/tas/cmip6/modified_data/monthly_values_plus_alt'
path_era5_tas = '/home/hchaabani/Data/tas/reanalysis/era5/modified_data/monthly_values_plus_alt'
path_era5_land_tas = '/home/hchaabani/Data/tas/reanalysis/era5_land/modified_data/monthly_values_plus_alt'
path_SIM_35km_tas = '/home/hchaabani/Data/tas/SIM_35km/modified_data/monthly_values_plus_alt'

cmip6_labels = os.listdir(path_cmip6_raw_data)
products_labels = ['era5_land','era5', 'SIM_35km'] + cmip6_labels

output_path_data = '/home/hchaabani/Hamid/PHD-mountain-climate/First_Part/Results/data/bias_correlations/'+bound+'/ref_'+ref+'/threshold_'+threshold
output_path_fig = '/home/hchaabani/Hamid/PHD-mountain-climate/First_Part/Results/figures/comparison/period_comparison/heatmaps/bias_correlations/'+bound+'/ref_'+ref+'/threshold_'+threshold

# Parameter to plot 
par1 = 'snc_monthly_value_15'    
par2 = 'ext_days_with_snow_15'   

dic_data_snc = {prod:'data' for prod in products_labels}
dic_data_pr = {prod:'data' for prod in products_labels}
dic_data_tas = {prod:'data' for prod in products_labels}

leg_title = 'correlation of bias'
max_leg = 1
min_leg = -1

# Dictionnaries of products titles 
y_titles = {'era5_land':'era5_land-10km','era5':'era5-25km',
            'SIM_35km':'lmdz-or-zo-ma-35km-or','BCC-CSM2-HR':'BCC-CSM2-HR',
            'EC-Earth3P-HR':'EC-Earth3P-HR-25km',
            'IPSL-CM6A-ATM-ICO-HR':'IPSL-CM6A-ATM-ICO-HR-50km',
            'IPSL-CM6A-ATM-ICO-VHR':'IPSL-CM6A-ATM-ICO-VHR-25km',
            'IPSL-CM6A-ATM-HR':'IPSL-CM6A-ATM-HR',
            'CNRM-CM6-1-HR':'CNRM-CM6-1-HR-50km'} 

In [4]:
products_labels.remove('BCC-CSM2-HR')

## Importing and preparing data 

### snc

In [5]:
for prod in products_labels[3:]:
    dic_data_snc[prod] = xr.open_dataset(path_cmip6_snc + '/snc_monthly_'+prod+'_plus_alt.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()

latlim = slice(34.5,30)   
dic_data_snc['era5_land'] = xr.open_dataset(path_era5_land_snc + '/snc_monthly_era5_land_plus_alt.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_snc['era5'] = xr.open_dataset(path_era5_snc + '/snc_monthly_era5_plus_alt.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_snc['SIM_35km'] = xr.open_dataset(path_SIM_35km_snc + '/snc_monthly_SIM_35km_plus_alt.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()

latlim = slice(30,34.5)

In [6]:
""" 
for prod in products_labels:  
    elevation = dic_data_snc[prod]['elevation']
    dic_data_snc[prod] = dic_data_snc[prod].where(dic_data_snc[prod]['elevation']>alt_min).where(dic_data_snc[prod]['elevation'] <= alt_max)
    dic_data_snc[prod]['elevation'] = elevation
"""

" \nfor prod in products_labels:  \n    elevation = dic_data_snc[prod]['elevation']\n    dic_data_snc[prod] = dic_data_snc[prod].where(dic_data_snc[prod]['elevation']>alt_min).where(dic_data_snc[prod]['elevation'] <= alt_max)\n    dic_data_snc[prod]['elevation'] = elevation\n"

### pr

In [7]:
for prod in products_labels[3:]:
    dic_data_pr[prod] = xr.open_dataset(path_cmip6_pr + '/pr_monthly_'+prod+'.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()

latlim = slice(34.5,30)   
dic_data_pr['era5_land'] = xr.open_dataset(path_era5_land_pr + '/pr_monthly_era5_land.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_pr['era5'] = xr.open_dataset(path_era5_pr + '/pr_monthly_era5.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_pr['SIM_35km'] = xr.open_dataset(path_SIM_35km_pr + '/pr_monthly_SIM_35km.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load() 

latlim = slice(30,34.5)

In [8]:
""" 
for prod in products_labels:  
    elevation = dic_data_pr[prod]['elevation']
    dic_data_pr[prod] = dic_data_pr[prod].where(dic_data_pr[prod]['elevation']>alt_min).where(dic_data_pr[prod]['elevation'] <= alt_max)
    dic_data_pr[prod]['elevation'] = elevation
"""

" \nfor prod in products_labels:  \n    elevation = dic_data_pr[prod]['elevation']\n    dic_data_pr[prod] = dic_data_pr[prod].where(dic_data_pr[prod]['elevation']>alt_min).where(dic_data_pr[prod]['elevation'] <= alt_max)\n    dic_data_pr[prod]['elevation'] = elevation\n"

### tas

In [9]:
for prod in products_labels[3:]:
    dic_data_tas[prod] = xr.open_dataset(path_cmip6_tas + '/tas_monthly_'+prod+'.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()

latlim = slice(34.5,30)   
dic_data_tas['era5_land'] = xr.open_dataset(path_era5_land_tas + '/tas_monthly_era5_land.nc').drop_duplicates(dim='time').sortby('time').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_tas['era5'] = xr.open_dataset(path_era5_tas + '/tas_monthly_era5.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()
dic_data_tas['SIM_35km'] = xr.open_dataset(path_SIM_35km_tas + '/tas_monthly_SIM_35km.nc').sel(time=period).sel(lat=latlim, lon=lonlim).load()        

In [10]:
products_labels

['era5_land',
 'era5',
 'SIM_35km',
 'EC-Earth3P-HR',
 'IPSL-CM6A-ATM-HR',
 'IPSL-CM6A-ATM-ICO-HR',
 'IPSL-CM6A-ATM-ICO-VHR',
 'CNRM-CM6-1-HR']

In [11]:
dic_data_pr['IPSL-CM6A-ATM-ICO-HR']

<xarray.Dataset>
Dimensions:    (time: 396, lon: 17, lat: 9)
Coordinates:
  * time       (time) datetime64[ns] 1982-01-16T12:00:00 ... 2014-12-16T12:00:00
  * lon        (lon) float32 -10.0 -9.5 -9.0 -8.5 -8.0 ... -3.5 -3.0 -2.5 -2.0
  * lat        (lat) float32 30.33 30.84 31.34 31.84 ... 32.84 33.34 33.84 34.35
Data variables:
    pr         (time, lat, lon) float32 5.055 4.434 2.713 ... 1.677 2.093 1.887
    elevation  (lat, lon) int16 0 156 387 1060 1470 1584 ... 609 418 428 763 411
Attributes: (12/44)
    CDI:                   Climate Data Interface version 2.0.4 (https://mpim...
    source:                IPSL-CM6A-ATM-ICO-HR (2021):  atmos: DYNAMICO-LMDZ...
    institution:           Institut Pierre Simon Laplace, Paris 75252, France
    Conventions:           CF-1.7 CMIP-6.2
    history:               Fri Sep 01 18:30:43 2023: cdo monmean pr_day_IPSL-...
    name:                  /ccc/work/cont003/gencmip6/p86caub/IGCM_OUT/ICOLMD...
    ...                    ...
    dr2xml_md5sum:         b6f602401512e82e2d7cadc2c6f36c2a
    model_version:         6.2.2
    nominal_resolution:    50 km
    grid:                  data regridded to a 720 x 360 longitude/latitude g...
    license:               CMIP6 model data produced by IPSL is licensed unde...
    CDO:                   Climate Data Operators version 2.0.4 (https://mpim...

In [12]:
dic_data_tas['IPSL-CM6A-ATM-ICO-HR']

<xarray.Dataset>
Dimensions:    (time: 396, lon: 17, lat: 9)
Coordinates:
  * time       (time) datetime64[ns] 1982-01-16T12:00:00 ... 2014-12-16T12:00:00
  * lon        (lon) float32 -10.0 -9.5 -9.0 -8.5 -8.0 ... -3.5 -3.0 -2.5 -2.0
  * lat        (lat) float32 30.33 30.84 31.34 31.84 ... 32.84 33.34 33.84 34.35
Data variables:
    tas        (time, lat, lon) float32 288.1 285.3 282.9 ... 282.2 281.5 281.1
    elevation  (lat, lon) int16 0 156 387 1060 1470 1584 ... 609 418 428 763 411
Attributes: (12/44)
    CDI:                   Climate Data Interface version 2.0.4 (https://mpim...
    source:                IPSL-CM6A-ATM-ICO-HR (2021):  atmos: DYNAMICO-LMDZ...
    institution:           Institut Pierre Simon Laplace, Paris 75252, France
    Conventions:           CF-1.7 CMIP-6.2
    history:               Fri Sep 01 18:58:44 2023: cdo monmean tas_day_IPSL...
    name:                  /ccc/work/cont003/gencmip6/p86caub/IGCM_OUT/ICOLMD...
    ...                    ...
    dr2xml_md5sum:         b6f602401512e82e2d7cadc2c6f36c2a
    model_version:         6.2.2
    nominal_resolution:    50 km
    grid:                  data regridded to a 720 x 360 longitude/latitude g...
    license:               CMIP6 model data produced by IPSL is licensed unde...
    CDO:                   Climate Data Operators version 2.0.4 (https://mpim...

In [13]:
""" 
for prod in products_labels:
    elevation = dic_data_tas[prod]['elevation']
    dic_data_tas[prod] = dic_data_tas[prod].where(dic_data_tas[prod]['elevation']>alt_min).where(dic_data_tas[prod]['elevation'] <= alt_max)
    dic_data_tas[prod]['elevation'] = elevation
"""

" \nfor prod in products_labels:\n    elevation = dic_data_tas[prod]['elevation']\n    dic_data_tas[prod] = dic_data_tas[prod].where(dic_data_tas[prod]['elevation']>alt_min).where(dic_data_tas[prod]['elevation'] <= alt_max)\n    dic_data_tas[prod]['elevation'] = elevation\n"

In [14]:
""" 
for prod in products_labels:
    print('============================== '+prod+' ===============================')
    print(dic_data_snc[prod])               
    print('=======================================================================')
"""

" \nfor prod in products_labels:\n    print('============================== '+prod+' ===============================')\n    print(dic_data_snc[prod])               \n    print('=======================================================================')\n"

## Calculate bias

In [15]:
ref_data_snc = dic_data_snc[ref]
ref_data_pr = dic_data_pr[ref]
ref_data_tas = dic_data_tas[ref]

products_labels.remove(ref)

dic_data_snc.pop(ref)
dic_data_pr.pop(ref)      
dic_data_tas.pop(ref)     

<xarray.Dataset>
Dimensions:    (time: 396, lon: 33, lat: 19)
Coordinates:
  * time       (time) datetime64[ns] 1982-01-16T11:00:00 ... 2014-12-16T11:00:00
  * lon        (lon) float32 -10.0 -9.75 -9.5 -9.25 ... -2.75 -2.5 -2.25 -2.0
  * lat        (lat) float32 34.5 34.25 34.0 33.75 ... 30.75 30.5 30.25 30.0
Data variables:
    tas        (time, lat, lon) float32 289.2 289.2 289.2 ... 284.3 284.1 283.9
    elevation  (lat, lon) int16 0 0 0 0 0 0 0 0 ... 323 318 309 297 283 259 124
Attributes:
    CDI:          Climate Data Interface version 2.0.4 (https://mpimet.mpg.de...
    Conventions:  CF-1.6
    history:      Fri Sep 01 18:44:16 2023: cdo monmean t2m_era5_1982-2014_da...
    frequency:    mon
    CDO:          Climate Data Operators version 2.0.4 (https://mpimet.mpg.de...

In [16]:
bias_means_snc = {prod:'data' for prod in products_labels}
bias_means_pr = {prod:'data' for prod in products_labels}
bias_means_tas = {prod:'data' for prod in products_labels}

ref_means_regridded_snc = {prod:'data' for prod in products_labels}   
ref_means_regridded_pr = {prod:'data' for prod in products_labels}   
ref_means_regridded_tas = {prod:'data' for prod in products_labels}   

In [17]:
if ref=='era5_land':
    for prod in products_labels:
        # snc
        regridder = xe.Regridder(ref_data_snc, dic_data_snc[prod],"conservative")
        ref_means_regridded_snc[prod] = regridder(ref_data_snc, keep_attrs=True)
        # pr
        regridder = xe.Regridder(ref_data_pr, dic_data_pr[prod],"conservative")
        ref_means_regridded_pr[prod] = regridder(ref_data_pr, keep_attrs=True)
        # tas
        regridder = xe.Regridder(ref_data_tas, dic_data_tas[prod],"conservative")
        ref_means_regridded_tas[prod] = regridder(ref_data_tas, keep_attrs=True)
        
        print('done for the product: '+prod)
    
if ref=='era5':
    for prod in products_labels[1:]:
        if prod == 'IPSL-CM6A-ATM-ICO-VHR':
            # snc
            regridder = xe.Regridder(dic_data_snc[prod], ref_data_snc,"conservative")
            dic_data_snc[prod] = regridder(dic_data_snc[prod], keep_attrs=True)
            ref_means_regridded_snc[prod] = ref_data_snc
            
            # pr
            regridder = xe.Regridder(dic_data_pr[prod], ref_data_pr,"conservative")
            dic_data_pr[prod] = regridder(dic_data_pr[prod], keep_attrs=True)
            ref_means_regridded_pr[prod] = ref_data_pr
    
            # tas
            regridder = xe.Regridder(dic_data_tas[prod], ref_data_tas,"conservative")
            dic_data_tas[prod] = regridder(dic_data_tas[prod], keep_attrs=True)
            ref_means_regridded_tas[prod] = ref_data_tas
        else:
            # snc
            regridder = xe.Regridder(ref_data_snc, dic_data_snc[prod],"conservative")
            ref_means_regridded_snc[prod] = regridder(ref_data_snc, keep_attrs=True)
        
            # pr
            regridder = xe.Regridder(ref_data_pr, dic_data_pr[prod],"conservative")
            ref_means_regridded_pr[prod] = regridder(ref_data_pr, keep_attrs=True)
        
            # tas
            regridder = xe.Regridder(ref_data_tas, dic_data_tas[prod],"conservative")
            ref_means_regridded_tas[prod] = regridder(ref_data_tas, keep_attrs=True)
        
        print('done for the product: '+prod)
        
    # snc
    regridder = xe.Regridder(dic_data_snc['era5_land'], ref_data_snc,"conservative")
    dic_data_snc['era5_land'] = regridder(dic_data_snc['era5_land'], keep_attrs=True)
    ref_means_regridded_snc['era5_land'] = ref_data_snc
    # pr
    regridder = xe.Regridder(dic_data_pr['era5_land'], ref_data_pr,"conservative")
    dic_data_pr['era5_land'] = regridder(dic_data_pr['era5_land'], keep_attrs=True)
    ref_means_regridded_pr['era5_land'] = ref_data_pr
    
    # tas
    regridder = xe.Regridder(dic_data_tas['era5_land'], ref_data_tas,"conservative")
    dic_data_tas['era5_land'] = regridder(dic_data_tas['era5_land'], keep_attrs=True)
    ref_means_regridded_tas['era5_land'] = ref_data_tas
    
    print('done for the product: era5_land')

done for the product: SIM_35km


/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/cf_xarray/accessor.py:1744: UserWarning: Variables {'lon_bnds'} not found in object but are referred to in the CF attributes.
  warnings.warn(
/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/cf_xarray/accessor.py:1744: UserWarning: Variables {'lon_bnds'} not found in object but are referred to in the CF attributes.
  warnings.warn(


done for the product: EC-Earth3P-HR
done for the product: IPSL-CM6A-ATM-HR
done for the product: IPSL-CM6A-ATM-ICO-HR
done for the product: IPSL-CM6A-ATM-ICO-VHR
done for the product: CNRM-CM6-1-HR
done for the product: era5_land


In [18]:
for prod in products_labels:
    print('============================== '+prod+' ===============================')
    print(ref_means_regridded_snc[prod])               
    print('=======================================================================')

============================== era5_land ===============================
<xarray.Dataset>
Dimensions:                (lon: 33, lat: 19, time: 396)
Coordinates:
  * lon                    (lon) float32 -10.0 -9.75 -9.5 ... -2.5 -2.25 -2.0
  * lat                    (lat) float32 34.5 34.25 34.0 ... 30.5 30.25 30.0
  * time                   (time) datetime64[ns] 1982-01-01 ... 2014-12-01
Data variables:
    snc_monthly_value      (time, lat, lon) float32 nan nan nan ... 0.0 0.0 0.0
    days_with_snow         (time, lat, lon) int32 0 0 0 0 0 0 0 ... 0 0 0 0 0 0
    days_without_snow      (time, lat, lon) int32 0 0 0 0 0 0 ... 31 31 31 31 31
    days_with_data         (time, lat, lon) int32 0 0 0 0 0 0 ... 31 31 31 31 31
    days_of_month          (time, lat, lon) int32 31 31 31 31 31 ... 31 31 31 31
    snc_monthly_value_15   (time, lat, lon) float32 nan nan nan ... 0.0 0.0 0.0
    days_with_snow_15      (time, lat, lon) float64 nan nan nan ... 0.0 0.0 0.0
    days_without_snow_15   (tim

In [19]:
for prod in products_labels:
    # snc (snow)
    elevation = dic_data_snc[prod]['elevation']
    bias_means_snc[prod] = dic_data_snc[prod].groupby('time.month').mean(dim='time') - ref_means_regridded_snc[prod].groupby('time.month').mean(dim='time')
    for mon in [1,2,3,4,5,6,7,8,9,10,11,12]:
        bias_means_snc[prod]['elevation'].loc[{'month':mon}] = elevation 
    dic_data_snc[prod] = dic_data_snc[prod].where(dic_data_snc[prod]['elevation']>alt_min).where(dic_data_snc[prod]['elevation']<=alt_max)
    
    # pr 
    elevation = dic_data_pr[prod]['elevation']
    bias_means_pr[prod] = dic_data_pr[prod].groupby('time.month').mean(dim='time') - ref_means_regridded_pr[prod].groupby('time.month').mean(dim='time')
    for mon in [1,2,3,4,5,6,7,8,9,10,11,12]:
        bias_means_pr[prod]['elevation'].loc[{'month':mon}] = elevation    
    dic_data_pr[prod] = dic_data_pr[prod].where(dic_data_pr[prod]['elevation']>alt_min).where(dic_data_pr[prod]['elevation']<=alt_max)

    # tas
    elevation = dic_data_tas[prod]['elevation']
    bias_means_tas[prod] = dic_data_tas[prod].groupby('time.month').mean(dim='time') - ref_means_regridded_tas[prod].groupby('time.month').mean(dim='time')
    for mon in [1,2,3,4,5,6,7,8,9,10,11,12]:
        bias_means_tas[prod]['elevation'].loc[{'month':mon}] = elevation
    dic_data_tas[prod] = dic_data_tas[prod].where(dic_data_tas[prod]['elevation']>alt_min).where(dic_data_tas[prod]['elevation']<=alt_max)
        
    print(' Done for the product: '+prod)

 Done for the product: era5_land
 Done for the product: SIM_35km
 Done for the product: EC-Earth3P-HR
 Done for the product: IPSL-CM6A-ATM-HR
 Done for the product: IPSL-CM6A-ATM-ICO-HR
 Done for the product: IPSL-CM6A-ATM-ICO-VHR
 Done for the product: CNRM-CM6-1-HR


###  Bias correlation 

In [20]:
dataframes_bias = { prod:{ mon:'data' for mon in months} for prod in products_labels }

In [21]:
for prod in products_labels:
    for mon in months:   
        df1 = bias_means_snc[prod][par1].loc[{'month':mon}].drop('month').to_dataframe().reset_index()[['lat','lon',par1]]
        df2 = bias_means_snc[prod][par2].loc[{'month':mon}].drop('month').to_dataframe().reset_index()[['lat','lon',par2]]
        df3 = bias_means_pr[prod].loc[{'month':mon}].drop('month').to_dataframe().reset_index()[['lat','lon','pr']]
        df4 = bias_means_tas[prod].loc[{'month':mon}].drop('month').to_dataframe().reset_index()[['lat','lon','tas']]
        """ 
        df1['lat'] = np.round(df1['lat'],2)
        df2['lat'] = np.round(df2['lat'],2)
        df3['lat'] = np.round(df3['lat'],2)
        df4['lat'] = np.round(df4['lat'],2)

        df1['lon'] = np.round(df1['lon'],2)
        df2['lon'] = np.round(df2['lon'],2)
        df3['lon'] = np.round(df3['lon'],2)
        df4['lon'] = np.round(df4['lon'],2)
        """
        df = pd.merge(df1,df2,on=['lon','lat'], how='inner')                       
        df = pd.merge(df, df3,on=['lon','lat'], how='inner')                        
        df = pd.merge(df, df4,on=['lon','lat'], how='inner')                         
        #df = df.dropna()                                                             
            
        dataframes_bias[prod][mon] = df                                       
                                                                  
    print('done for the prod: '+prod)         
        
        
"""    
        if prod == 'BCC-CSM2-HR':
            regridder = xe.Regridder(df3.set_index(['lon','lat']).to_xarray(), df1.set_index(['lon','lat']).to_xarray(),"conservative")
            df3 = regridder(df3.set_index(['lon','lat']).to_xarray(), keep_attrs=True)
            df3 = df3.to_dataframe().reset_index()
        
            df = pd.merge(df1, df2,on=['lon','lat'], how='inner')
            df = pd.merge(df, df3,on=['lon','lat'], how='inner')
        
            regridder = xe.Regridder(df.set_index(['lon','lat']).to_xarray(), df4.set_index(['lon','lat']).to_xarray(),"conservative")
            df = regridder(df.set_index(['lon','lat']).to_xarray(), keep_attrs=True)
            df = df.to_dataframe().reset_index()
   
            df = pd.merge(df, df4,on=['lon','lat'], how='inner')                      
    
            df = df.dropna()                         
            dataframes_bias[prod][mon] = df                       

""" 
                                                                                           

done for the prod: era5_land
done for the prod: SIM_35km
done for the prod: EC-Earth3P-HR
done for the prod: IPSL-CM6A-ATM-HR
done for the prod: IPSL-CM6A-ATM-ICO-HR
done for the prod: IPSL-CM6A-ATM-ICO-VHR
done for the prod: CNRM-CM6-1-HR


'    \n        if prod == \'BCC-CSM2-HR\':\n            regridder = xe.Regridder(df3.set_index([\'lon\',\'lat\']).to_xarray(), df1.set_index([\'lon\',\'lat\']).to_xarray(),"conservative")\n            df3 = regridder(df3.set_index([\'lon\',\'lat\']).to_xarray(), keep_attrs=True)\n            df3 = df3.to_dataframe().reset_index()\n        \n            df = pd.merge(df1, df2,on=[\'lon\',\'lat\'], how=\'inner\')\n            df = pd.merge(df, df3,on=[\'lon\',\'lat\'], how=\'inner\')\n        \n            regridder = xe.Regridder(df.set_index([\'lon\',\'lat\']).to_xarray(), df4.set_index([\'lon\',\'lat\']).to_xarray(),"conservative")\n            df = regridder(df.set_index([\'lon\',\'lat\']).to_xarray(), keep_attrs=True)\n            df = df.to_dataframe().reset_index()\n   \n            df = pd.merge(df, df4,on=[\'lon\',\'lat\'], how=\'inner\')                      \n    \n            df = df.dropna()                         \n            dataframes_bias[prod][mon] = df               

In [22]:
correlations = {mon: pd.DataFrame(columns=['index']+products_labels) for mon in months}
significances = {mon: pd.DataFrame(columns=['index']+products_labels) for mon in months}
sig_mask = {mon: pd.DataFrame(columns=['index']+products_labels) for mon in months}

In [23]:
for mon in months:               
    correlations[mon]['index'] = ['snc bias/pr bias','snc bias/tas bias',
                                  'duration bias/pr bias','duration bias/tas bias',
                                  'tas bias/pr bias']
    
    significances[mon]['index'] = ['snc bias/pr bias','snc bias/tas bias',
                                  'duration bias/pr bias','duration bias/tas bias',
                                  'tas bias/pr bias']
    
    sig_mask[mon]['index'] =  ['snc bias/pr bias','snc bias/tas bias',
                                  'duration bias/pr bias','duration bias/tas bias',
                                  'tas bias/pr bias']
    

In [24]:
for mon in months:
    correlations[mon] = correlations[mon].set_index('index')
    significances[mon] = significances[mon].set_index('index')
    sig_mask[mon] = sig_mask[mon].set_index('index')

In [25]:
for mon in months:
    for prod in products_labels:
        if len(dataframes_bias[prod][mon][[par1,'pr']].dropna()[par1])>1:
            cor_coef, p_value = pearsonr(dataframes_bias[prod][mon][[par1,'pr']].dropna()[par1], dataframes_bias[prod][mon][[par1,'pr']].dropna()['pr'])
            correlations[mon].loc['snc bias/pr bias'][prod] = cor_coef
            significances[mon].loc['snc bias/pr bias'][prod] = p_value
        else: 
            cor_coef, p_value = np.nan, np.nan
            correlations[mon].loc['snc bias/pr bias'][prod] = cor_coef
            significances[mon].loc['snc bias/pr bias'][prod] = p_value
            

        if len(dataframes_bias[prod][mon][[par1,'tas']].dropna()[par1])>1:
            cor_coef, p_value = pearsonr(dataframes_bias[prod][mon][[par1,'tas']].dropna()[par1], dataframes_bias[prod][mon][[par1,'tas']].dropna()['tas'])
            correlations[mon].loc['snc bias/tas bias'][prod] = cor_coef
            significances[mon].loc['snc bias/tas bias'][prod] = p_value
        else:
            cor_coef, p_value = np.nan, np.nan
            correlations[mon].loc['snc bias/tas bias'][prod] = cor_coef
            significances[mon].loc['snc bias/tas bias'][prod] = p_value         
            
            
        if len(dataframes_bias[prod][mon][[par2,'pr']].dropna()[par2])>1:  
            cor_coef, p_value = pearsonr(dataframes_bias[prod][mon][[par2,'pr']].dropna()[par2], dataframes_bias[prod][mon][[par2,'pr']].dropna()['pr'])
            correlations[mon].loc['duration bias/pr bias'][prod] = cor_coef
            significances[mon].loc['duration bias/pr bias'][prod] = p_value
        else:
            cor_coef, p_value = np.nan, np.nan            
            correlations[mon].loc['duration bias/pr bias'][prod] = cor_coef
            significances[mon].loc['duration bias/pr bias'][prod] = p_value            
            
            
        if len(dataframes_bias[prod][mon][[par2,'tas']].dropna()[par2])>1:  
            cor_coef, p_value = pearsonr(dataframes_bias[prod][mon][[par2,'tas']].dropna()[par2], dataframes_bias[prod][mon][[par2,'tas']].dropna()['tas'])
            correlations[mon].loc['duration bias/tas bias'][prod] = cor_coef
            significances[mon].loc['duration bias/tas bias'][prod] = p_value
        else:
            cor_coef, p_value = np.nan, np.nan            
            correlations[mon].loc['duration bias/tas bias'][prod] = cor_coef
            significances[mon].loc['duration bias/tas bias'][prod] = p_value
            
            
        if len(dataframes_bias[prod][mon][['pr','tas']].dropna()['tas'])>1:  
            cor_coef, p_value = pearsonr(dataframes_bias[prod][mon][['pr','tas']].dropna()['pr'], dataframes_bias[prod][mon][['pr','tas']].dropna()['tas'])
            correlations[mon].loc['tas bias/pr bias'][prod] = cor_coef
            significances[mon].loc['tas bias/pr bias'][prod] = p_value
        else:
            cor_coef, p_value = np.nan, np.nan            
            correlations[mon].loc['tas bias/pr bias'][prod] = cor_coef
            significances[mon].loc['tas bias/pr bias'][prod] = p_value
                        
    print('done for the month: '+str(mon))

done for the month: 11
done for the month: 12
done for the month: 1
done for the month: 2
done for the month: 3
done for the month: 4


In [26]:
for mon in months:
    sig_mask[mon] = np.where(significances[mon]<=0.05,0,1)

In [27]:
#for mon in months:
#    correlations[mon].to_excel(output_path_data+'/bias_correlation_month_'+str(mon)+'_ref_'+ref+'_threshold_'+threshold+'.xlsx')
#    significances[mon].to_excel(output_path_data+'/bias_correlation_significance_month_'+str(mon)+'_ref_'+ref+'_threshold_'+threshold+'.xlsx')    

## Plots


<div class="alert alert-block alert-success"; background-color:red> We define the figures formatting function </div> 

In [28]:
# This auxiliary function will help us in the formatting of the figures
def set_size(w,h, ax=None):
    """ w, h: width, height in inches """
    if not ax: ax=plt.gca()
    l = ax.figure.subplotpars.left
    r = ax.figure.subplotpars.right
    t = ax.figure.subplotpars.top
    b = ax.figure.subplotpars.bottom
    figw = float(w)/(r-l)
    figh = float(h)/(t-b)
    ax.figure.set_size_inches(figw, figh)

In [29]:
y_labels = ['snc bias/pr bias',
 'snc bias/tas bias',
 'dur bias/pr bias',
 'dur bias/tas bias',
 'tas bias/pr bias']

In [30]:

fig, axs = plt.subplots(nrows=6,ncols=1, dpi=500)     
# Formatting figure                
plt.subplots_adjust(wspace=0.3,hspace=0.3)   
set_size(16,20)  

"""                       
Axs is a 2 dimensional array of `GeoAxes`.  We will flatten it into 
a 1-D array as follow 
"""                       
axs=axs.flatten()

# Add a colorbar axis at the left side of the figure  
cbar_ax = fig.add_axes([0.92, 0.115, 0.02, 0.766])
    
for imon,mon in enumerate(months):
    data = [list(correlations[mon].loc['snc bias/pr bias']),
             list(correlations[mon].loc['snc bias/tas bias']),
            list(correlations[mon].loc['duration bias/pr bias']),
            list(correlations[mon].loc['duration bias/tas bias']),
            list(correlations[mon].loc['tas bias/pr bias'])]
    
    if imon==2:
        c_map = sns.heatmap(data,ax=axs[imon],annot=True,fmt=".2f",
                            annot_kws={'size':18,"fontweight":"bold"},cbar=True,
                            cbar_ax=cbar_ax, cmap='seismic',vmin=-1,
                            vmax=1) 
    
    else:
        sns.heatmap(data,ax=axs[imon],annot=True,fmt=".2f",
                            annot_kws={'size':18,"fontweight":"bold"},cbar=False,
                    cmap='seismic',vmin=-1,vmax=1) # mask=sig_mask[mon] 

    # Add hatches for non significant correlations 
    for i in range(np.array(data).shape[0]):
        for j in range(np.array(data).shape[1]):
            if np.abs(data[i][j]) > 0.5:
                color = 'white'
                hatches = ' \\\\ '
            if np.abs(data[i][j]) <= 0.5: 
                color='black'
                hatches = ' \\\\ '
            if np.isnan(data[i][j]):
                hatches = ' '
                color = 'white'
            if sig_mask[mon][i][j] == 1:
                axs[imon].text(j + 0.5, i + 0.5, hatches, 
                         horizontalalignment='center',
                     verticalalignment='center', color=color,
                         fontsize=36)
    
    axs[imon].set_ylabel('')    
    axs[imon].set_yticklabels(labels=y_labels, 
                              rotation =0, fontsize=16,fontweight= "bold")   
    axs[imon].set_xticklabels(labels=[])   

    axs[imon].set_title(months_titles[mon], fontsize=24,
                        fontweight= "bold")
    
axs[5].set_xticklabels(labels=products_labels, rotation = 30, 
                       fontsize=18,fontweight= "bold") 
                
# Formatting c_bar                     
c_bar = c_map.collections[0].colorbar     
c_bar.set_ticks([i for i in np.round(np.arange(-1,1.2,0.2),2)])    
c_bar.set_ticklabels([i for i in np.round(np.arange(-1,1.2,0.2),2)])    
c_bar.ax.tick_params(labelsize=24)     
c_bar.set_label('correlation',fontsize=26,fontweight= "bold")                

# Store figures                                                                                                         
#plt.savefig(output_path_fig+'/bias_correlation_ref_'+ref+'_threshold_'+threshold+'_without_BCC.pdf')         
#plt.savefig(output_path_fig+'/bias_correlation_ref_'+ref+'_threshold_'+threshold+'_without_BCC.png')       

/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/IPython/core/pylabtools.py:152: MatplotlibDeprecationWarning: savefig() got unexpected keyword argument "orientation" which is no longer supported as of 3.3 and will become an error two minor releases later
  fig.canvas.print_figure(bytes_io, **kw)
/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/IPython/core/pylabtools.py:152: MatplotlibDeprecationWarning: savefig() got unexpected keyword argument "facecolor" which is no longer supported as of 3.3 and will become an error two minor releases later
  fig.canvas.print_figure(bytes_io, **kw)
/home/hchaabani/anaconda3/envs/first_part/lib/python3.11/site-packages/IPython/core/pylabtools.py:152: MatplotlibDeprecationWarning: savefig() got unexpected keyword argument "edgecolor" which is no longer supported as of 3.3 and will become an error two minor releases later
  fig.canvas.print_figure(bytes_io, **kw)
/home/hchaabani/anaconda3/envs/first_part/li